In [1]:
import sys
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [5]:
expr = pd.DataFrame(pd.read_csv("GSE142432_normalized_counts.csv", sep=",", header=0))
ih_df = pd.read_csv("GSE142432-GPL17021-ih.txt", sep="\t", header=0) 
expr.columns = ["ProbeID"]+list(ih_df["ArrayID"])+["Name", "Description"]
cols = ["ProbeID", "Name"]+list(ih_df["ArrayID"])
expr = expr[cols]
expr

ProbeID           Name   GSM4227302   GSM4227303  \
0      ENSMUSG00000000001          Gnai3   503.443897   507.436879   
1      ENSMUSG00000000028          Cdc45    10.989774     3.703919   
2      ENSMUSG00000000056           Narf   234.058809   233.346886   
3      ENSMUSG00000000058           Cav2     1.169125    11.111756   
4      ENSMUSG00000000078           Klf6  1509.821952  1211.181456   
...                   ...            ...          ...          ...   
10291  ENSMUSG00000109511          Nup62    13.328024    11.111756   
10292  ENSMUSG00000109550   RP23-218E6.1     5.377975    11.111756   
10293  ENSMUSG00000109554  RP24-274B19.1     1.627422    11.111756   
10294  ENSMUSG00000109555   RP23-218E6.3     3.975025    18.519594   
10295  ENSMUSG00000109556   RP23-81F19.2     2.572075     3.703919   

        GSM4227304   GSM4227305   GSM4227306   GSM4227307   GSM4227308  \
0       279.799805   240.119491   266.276087   428.314279   447.481191   
1         7.903949    10.780875     7.607888     6.171675     3.003229   
2       156.502712   129.923266   169.909503   183.915930   255.274505   
3         0.225827     0.196016     2.535963     1.234335     3.003229   
4      1903.112908  1489.172081  1174.150747  1238.038105  1258.353149   
...            ...          ...          ...          ...          ...   
10291    21.001922     8.428684    32.967516     8.640346    33.035524   
10292     2.484098     2.156175    17.751739     1.234335     3.003229   
10293     2.055027     0.196016     2.535963     6.171675     3.003229   
10294     8.355604     4.116334     2.535963     8.640346    15.016147   
10295     3.839061     3.332270     2.535963     3.703005     3.003229   

       GSM4227309   GSM4227310   GSM4227311  GSM4227312  GSM4227313  \
0      323.945741   447.561820   359.736582  402.967110  422.635274   
1       11.433379    17.127990     7.053658    6.640259   12.831532   
2      232.478708   161.598860   157.531706  194.982138  196.897650   
3        3.811126     0.744695     2.351219  167.213784  151.766053   
4      743.169641  1085.020919  1210.878037  636.849091  860.571044   
...           ...          ...          ...         ...         ...   
10291   26.677885    17.127990    21.160975    5.432939   10.176732   
10292    3.811126     2.234086     2.351219    1.810980    2.212333   
10293    3.811126     0.744695     2.351219    0.603660    1.336249   
10294    3.811126     8.191647     2.351219    1.810980    3.097266   
10295    3.811126     2.234086     2.351219    0.603660    3.097266   

       GSM4227314  GSM4227315  GSM4227316  GSM4227317  
0      373.723469  355.717818  382.664885  319.116960  
1        9.423549    6.897575   12.235767   11.973393  
2      187.746098  160.614971  171.883399   97.348893  
3      235.588733   87.697745   90.311616  108.801704  
4      818.558490  702.547618  848.789357  589.819765  
...           ...         ...         ...         ...  
10291   31.170202    8.868311   18.062323   14.055723  
10292    2.174665    2.956104    0.582656    0.520582  
10293    2.174665    2.956104    1.747967    2.592500  
10294    0.724888    0.985368    1.747967    1.561747  
10295    2.174665    4.926840    4.078589    0.520582  

[10296 rows x 18 columns]

In [6]:
genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
#sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

path_dir = "./"
expr.to_csv(path_dir+"GSE154311-GPL18573-expr.txt", header=True, index=False,sep='\t')
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID           Name  GSM4227302  GSM4227303  GSM4227304  \
0      ENSMUSG00000000001          Gnai3    8.978550    8.989924    8.133398   
1      ENSMUSG00000000028          Cdc45    3.583733    2.233863    3.154445   
2      ENSMUSG00000000056           Narf    7.876878    7.872502    7.299232   
3      ENSMUSG00000000058           Cav2    1.117113    3.598336    0.293756   
4      ENSMUSG00000000078           Klf6   10.561118   10.243390   10.894903   
...                   ...            ...         ...         ...         ...   
10291  ENSMUSG00000109511          Nup62    3.840768    3.598336    4.459558   
10292  ENSMUSG00000109550   RP23-218E6.1    2.673098    3.598336    1.800785   
10293  ENSMUSG00000109554  RP24-274B19.1    1.393648    3.598336    1.611185   
10294  ENSMUSG00000109555   RP23-218E6.3    2.314704    4.286851    3.225831   
10295  ENSMUSG00000109556   RP23-81F19.2    1.836762    2.233863    2.274727   

       GSM4227305  GSM4227306  GSM4227307  GSM4227308  GSM4227309  GSM4227310  \
0        7.913604    8.062187    8.745890    8.808904    8.344055    8.809163   
1        3.558375    3.105659    2.842310    2.001164    3.636147    4.180147   
2        7.032578    7.417089    7.530725    8.001547    7.867147    7.345173   
3        0.258237    1.822103    1.159846    2.001164    2.266375    0.802975   
4       10.541264   10.198630   10.275005   10.298467    9.539488   10.084836   
...           ...         ...         ...         ...         ...         ...   
10291    3.237056    5.086084    3.269085    5.088969    4.790662    4.180147   
10292    1.658177    4.228952    1.159846    2.001164    2.266375    1.693358   
10293    0.258237    1.822103    2.842310    2.001164    2.266375    0.802975   
10294    2.355110    1.822103    3.269085    4.001455    2.266375    3.200323   
10295    2.115123    1.822103    2.233583    2.001164    2.266375    1.693358   

       GSM4227311  GSM4227312  GSM4227313  GSM4227314  GSM4227315  GSM4227316  \
0        8.494802    8.658093    8.726679    8.549683    8.478640    8.583703   
1        3.009645    2.933622    3.789889    3.381775    2.981410    3.726370   
2        7.308628    7.614579    7.628610    7.560303    7.336417    7.433656   
3        1.744686    7.394152    7.255180    7.886238    6.470825    6.512726   
4       10.243029    9.317071    9.750826    9.678703    9.458505    9.730962   
...           ...         ...         ...         ...         ...         ...   
10291    4.469949    2.685478    3.482426    5.007653    3.302803    4.252652   
10292    1.744686    1.491073    1.683622    1.666604    1.984080    0.662347   
10293    1.744686    0.681368    1.224194    1.666604    1.984080    1.458365   
10294    1.744686    1.491073    2.034662    0.786503    0.989406    1.458365   
10295    1.744686    0.681368    2.034662    1.666604    2.567263    2.344428   

       GSM4227317  
0        8.322455  
1        3.697484  
2        6.619837  
3        6.778757  
4        9.206574  
...           ...  
10291    3.912240  
10292    0.604624  
10293    1.844988  
10294    1.357128  
10295    0.604624  

[10296 rows x 18 columns]

In [7]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE142432-GPL17021-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE142432-GPL17021-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
